In [1]:
import pickle
import numpy as np
import pandas as pd

In [2]:
# with open("data_storage/small_dataset.obj", "rb") as file:
#     data = pickle.load(file)

# If you want to use main data download it from here: https://zenodo.org/record/7437768#.Y6W6YnaZO5d
# Then move the downloaded file to the data_storage folder
with open("data_storage/Extended_manhattan_pooling.obj", "rb") as file:
    data = pickle.load(file)

In [4]:
data[0]["requests"][:3]

id     pickup_datetime     dropoff_datetime  trip_duration  \
0  id0190469 2016-01-01 00:00:17  2016-01-01 00:14:26            849   
1  id1210365 2016-01-01 00:01:01  2016-01-01 00:07:49            408   
2  id3991965 2016-01-01 00:20:08  2016-01-01 00:29:16            548   

     origin  destination  status   dist  treq  ttrav  ...    u_PT  ride_id  \
0  42427352     42438018       0  14340     0   2390  ...  999999      306   
1  42432756     42434113       0   2640    44    440  ...  999999        1   
2  42437917     42434113       0   2705  1191    450  ...  999999      118   

   ttrav_sh       u_sh  kind  position      x_org      y_org     x_dest  \
0      2591  29.772825    21         0 -73.981942  40.719462 -73.938959   
1       440   5.500000     1         0 -73.965196  40.801107 -73.947489   
2       450   5.632500     1         0 -73.963370  40.798568 -73.947489   

      y_dest  
0  40.828984  
1  40.815207  
2  40.815207  

[3 rows x 24 columns]

In [5]:
concatenated_data = pd.concat([d["requests"] for d in data])

In [18]:
concatenated_data[:3]

id     pickup_datetime     dropoff_datetime  trip_duration  \
0  id0190469 2016-01-01 00:00:17  2016-01-01 00:14:26            849   
1  id1210365 2016-01-01 00:01:01  2016-01-01 00:07:49            408   
2  id3991965 2016-01-01 00:20:08  2016-01-01 00:29:16            548   

     origin  destination  status   dist  treq  ttrav  ... ride_id  ttrav_sh  \
0  42427352     42438018       0  14340     0   2390  ...     306      2591   
1  42432756     42434113       0   2640    44    440  ...       1       440   
2  42437917     42434113       0   2705  1191    450  ...     118       450   

        u_sh  kind  position      x_org      y_org     x_dest     y_dest  \
0  29.772825    21         0 -73.981942  40.719462 -73.938959  40.828984   
1   5.500000     1         0 -73.965196  40.801107 -73.947489  40.815207   
2   5.632500     1         0 -73.963370  40.798568 -73.947489  40.815207   

        h3_address  
0  8a2a100d378ffff  
1  8a2a10088857fff  
2  8a2a10088b17fff  

[3 rows x 25 columns]

In [19]:
len(concatenated_data)

4908349

In [20]:
import h3
import folium
from geojson.feature import Feature, FeatureCollection
import json
import osmnx as ox

In [32]:
# add hexagon column to the DataFrame
df = concatenated_data
zoning_level = 10
df['h3_address'] = df.apply(lambda row: h3.geo_to_h3(row.y_org, row.x_org, zoning_level), axis=1)
df['del_PassHourTrav']=abs((df['ttrav']-df['ttrav_sh'])/df['ttrav_sh'])
df['del_PassUtility']=abs((df['u']-df['u_sh'])/df['u_sh'])
# df

In [33]:
# Here are some visualization functions to check the hexagons without colorbar.

def visualize_hexagons(hexagons, color="red", w=1, folium_map=None):
    """
    hexagons is a list of hexcluster. Each hexcluster is a list of hexagons. 
    eg. [[hex1, hex2], [hex3, hex4]]
    """
    polylines = []
    lat = []
    lng = []
    for hex in hexagons:
        polygons = h3.h3_set_to_multi_polygon([hex], geo_json=False)
        # flatten polygons into loops.
        outlines = [loop for polygon in polygons for loop in polygon]
        polyline = [outline + [outline[0]] for outline in outlines][0]
        lat.extend(map(lambda v:v[0],polyline))
        lng.extend(map(lambda v:v[1],polyline))
        polylines.append(polyline)
    
    if folium_map is None:
        m = folium.Map(location=[sum(lat)/len(lat), sum(lng)/len(lng)], zoom_start=13, tiles='cartodbpositron')
    else:
        m = folium_map
    for polyline in polylines:
        my_PolyLine=folium.PolyLine(locations=polyline,weight=w,color=color,fill= True)
        m.add_child(my_PolyLine)
    return m
    

def visualize_polygon(polyline, color):
    polyline.append(polyline[0])
    lat = [p[0] for p in polyline]
    lng = [p[1] for p in polyline]
    m = folium.Map(location=[sum(lat)/len(lat), sum(lng)/len(lng)], zoom_start=13, tiles='cartodbpositron')
    my_PolyLine=folium.PolyLine(locations=polyline,weight=8,color=color)
    m.add_child(my_PolyLine)
    return m

In [34]:
# Using the above function you can visualize the hexagons.

hexagons = list(df.h3_address.unique())
visualize_hexagons(hexagons, color="red", w=1, folium_map=None)

In [35]:
# to plot the KPIs you need to groupby the requests by their hexagon address
# according to you purpose you may use groupby().mean() or groupby().sum()

df_new = df.groupby(['h3_address']).mean()
df_new.reset_index(inplace=True)
# df_new

C:\Users\shuli\AppData\Local\Temp\ipykernel_18116\454512563.py:4: FutureWarning: The default value of numeric_only in DataFrameGroupBy.mean is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.
  df_new = df.groupby(['h3_address']).mean()


In [36]:
# use this function to get the plots with colorbar.
# adjust the bins before plotting. Otherwise you will see an error.
# you may also modify the other features like colors, opacity and line_weight. 

def h3_visualization(df, hex_col, value_col):
    df['lat'] = df[hex_col].apply(lambda x: h3.h3_to_geo(x)[0])
    df['lng'] = df[hex_col].apply(lambda x: h3.h3_to_geo(x)[1])
    # df.set_index('hex_address', inplace=True)
    df['geom'] = df.apply(lambda x: {"type": "Polygon","coordinates": [h3.h3_to_geo_boundary(h = x[hex_col], geo_json = True)]}, axis = 1)
    list_features = []
    for i, row in df.iterrows():
            feature = Feature(geometry = row["geom"],
                              id = row[hex_col],
                              properties = {"resolution": 9})
            list_features.append(feature)
    list_features 

    feat_collection = FeatureCollection(list_features)
    geojson_hexes = json.dumps(feat_collection)
    geojson_hexes

    # cx, cy = G.nodes[centeral_node]['x'], G.nodes[centeral_node]['y']
    # CENTER = [cy, cx]
    CENTER = [h3.h3_to_geo(df.loc[0][hex_col])[0], h3.h3_to_geo(df.loc[0][hex_col])[1]]

    tile = 'cartodbpositron'
    base_map = folium.Map(zoom_start=11,tiles=tile, zoomControl =  False, location=CENTER)
    
    step = (df[value_col].max() - df[value_col].min())/5
    print(df[value_col].min(),'  ', df[value_col].max()+step, '  ', step)
    bins = list(np.arange(df[value_col].min(),df[value_col].max()+step,step))
    # bins = list(np.arange(0, 100000, 20000))
    # bins = [0,20000,40000,60000,80000,1000000]

    # for colors see https://user-images.githubusercontent.com/17128994/115975254-c2031e00-a56b-11eb-8025-d82d36bfda1d.png
    color_set = ["Spectral", "RdYlGn", "PuBu", "Accent", "OrRd", "Set1", "Set2", "Set3", "BuPu", "Dark2", "RdBu", "Oranges", "BuGn", "PiYG", "YlOrBr", "YlGn", "Pastel2", "RdPu", "Greens", "PRGn", "YlGnBu", "RdYlBu", "Paired", "BrBG", "Purples", "Reds", "Pastel1", "GnBu", "Greys", "RdGy", "YlOrRd", "PuOr", "PuRd", "Blues", "PuBuGn"]
    m = folium.Choropleth(geo_data = geojson_hexes,data = df, columns = [hex_col,value_col],key_on ="feature.id",
            fill_color='Reds', control = False, bins = bins, line_weight=1, legend_name='',
            fill_opacity=0.5, line_opacity=0.2).add_to(base_map)

    return base_map

In [37]:
h3_visualization(df_new, 'h3_address', 'del_PassUtility')

0.0    0.1257149927706668    0.020952498795111133


In [38]:
h3_visualization(df_new, 'h3_address', 'del_PassUtility')

0.0    0.1257149927706668    0.020952498795111133


In [39]:
# to get a plot for number of request for each hexagon I add a column of ones and 
# then use groupby().sum() But you may use another method

df['number_of_req'] = 1
df['number_of_req_sh'] = np.where(df['kind']!= 1, 1, 0) # to get a number of pooled request 
df_new = df.groupby(['h3_address']).sum()
df_new.reset_index(inplace=True)
df_new['S']=np.where(df_new['number_of_req_sh']!=0,df_new['number_of_req_sh']/df_new['number_of_req'],0) # to get a shared ratio for each hexagon
df_new

C:\Users\shuli\AppData\Local\Temp\ipykernel_18116\1997548074.py:6: FutureWarning: The default value of numeric_only in DataFrameGroupBy.sum is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.
  df_new = df.groupby(['h3_address']).sum()


h3_address  trip_duration         origin   destination  status  \
0     8a2a1008800ffff           3364     4762512960    2050585708       0   
1     8a2a1008801ffff          25384    25074148160     848829408       0   
2     8a2a10088027fff          23964      848591140     848793240       0   
3     8a2a1008802ffff          11664     1188338360   30361469336       0   
4     8a2a10088047fff         590044    34623776784  349726330200       0   
...               ...            ...            ...           ...     ...   
2241  8a2a1072dd97fff         928834   401250052118  447821782530       0   
2242  8a2a1072dd9ffff        2112978  1436396966376  889345609503       0   
2243  8a2a1072dda7fff         395912    23093933696  318062700008       0   
2244  8a2a1072ddaffff         176818    11842327143  153867097336       0   
2245  8a2a1072ddb7fff          51196     3395649600   27922888172       0   

         dist     treq    ttrav     VoT          delta  ...          x_org  \
0       15032    10300     2504  0.0280     710.610989  ...    -591.792917   
1      128508    19024    21412  0.0700    6073.740659  ...   -1479.513740   
2       94848    11448    15800  0.0700    4483.674725  ...   -1479.462896   
3       50576    18060     8412  0.0980    2393.854945  ...   -2071.257576   
4     2774576   707528   462100  2.8560  131182.338462  ...  -60362.135362   
...       ...      ...      ...     ...            ...  ...            ...   
2241  2447928   697662   407680  2.7650  115742.400000  ...  -58453.546571   
2242  6330143  1622262  1054262  6.4645  299471.287912  ... -136663.551126   
2243  1747868   519116   291096  1.9040   82641.257143  ...  -40250.097274   
2244   741667   236496   123504  0.9765   35080.602198  ...  -20643.139748   
2245   188768    72868    31432  0.2800    8926.575824  ...   -5919.304952   

             y_org         x_dest        y_dest  del_VehHourTrav  \
0       326.372181    -591.757966    326.386736         0.000000   
1       815.944058   -1479.733475    815.059383        -0.651693   
2       815.971630   -1479.669615    815.256232        -1.011876   
3      1142.337989   -2071.196351   1142.258304        -0.112676   
4     33288.926040  -60361.890584  33276.245930       -20.914847   
...            ...            ...           ...              ...   
2241  32165.788427  -58453.326710  32180.412747       -16.585808   
2242  75200.403046 -136656.448217  75242.809333       -52.706646   
2243  22149.891219  -40247.543416  22160.829776       -11.679328   
2244  11359.641435  -20642.671872  11364.307957        -5.856386   
2245   3257.282544   -5919.422978   3258.276026        -1.229506   

      del_PassUtility  del_PassHourTrav  number_of_req  number_of_req_sh  \
0            0.098637          0.000000              8                 2   
1            0.226633          0.651693             20                 5   
2            0.588846          1.011876             20                12   
3            0.102105          0.112676             28                 2   
4           16.152045         20.949118            816               313   
...               ...               ...            ...               ...   
2241        11.103132         16.594091            790               226   
2242        33.561613         52.720516           1847               683   
2243        10.391610         11.680941            544               193   
2244         4.491771          5.856386            279                96   
2245         0.948342          1.229506             80                17   

             S  
0     0.250000  
1     0.250000  
2     0.600000  
3     0.071429  
4     0.383578  
...        ...  
2241  0.286076  
2242  0.369789  
2243  0.354779  
2244  0.344086  
2245  0.212500  

[2246 rows x 27 columns]

In [40]:
h3_visualization(df_new, 'h3_address', 'number_of_req')

4    71549.2    11924.2


In [41]:
h3_visualization(df_new, 'h3_address', 'S')

0.0    1.2    0.2
